### 네이버 뉴스기사

In [ ]:
!pip install selenium
!apt-get update
!apt install -y chromium-chromedriver
!cp /usr/lib/chromium-browser/chromedriver /usr/bin
!pip install webdriver-manager

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 65.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.3/486.3 kB 27.1 MB/s eta 0:00:00
Get:1 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Get:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Get:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease [1,581 B]
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Get:6 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:7 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ Packages [62.5 kB]
Get:8 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  Packages [1,234 kB]
Get:9 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [127 kB]
Hit:10 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Get:11 https://r2u.stat.illinois.edu/ubuntu jam

In [ ]:
import requests
import json
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
from bs4 import BeautifulSoup
# https://openapi.naver.com/v1/search/blog.json
# https://openapi.naver.com/v1/search/news.json

# https://blog.naver.com/
# https://n.news.naver.com/mnews/article

# 최근 AI 업계에서 비디오 생성 모델이 뭐가 있을까? 그리고 그 모델들의 성능 비교는 어떻게 되고, 앞으로의 전망은 어때?

def fetch_naver_news(max_articles=50):
    url = "https://openapi.naver.com/v1/search/news.json"
    headers = {
        "X-Naver-Client-Id": "",
        "X-Naver-Client-Secret": ""
    }
    params = {
        "query": "AI의 사회적 영향",
        "display": 100,
        "start": 1,
        "sort": "sim"
    }

    api_call_count = 0
    articles_fetched = 0

    naver_news = []  # 기사 정보를 담을 리스트 변수 naver_news

    while articles_fetched < max_articles:
        api_call_count += 1
        print(f"API 호출 횟수: {api_call_count}")

        response = requests.get(url, headers=headers, params=params)

        if response.status_code == 200:
            try:
                data = response.json()

                for i, item in enumerate(data["items"]):
                    article_url = item["link"]

                    if not article_url.startswith("https://n.news.naver.com/mnews/article"):
                        continue

                    print(f"네이버 뉴스 링크 발견: {article_url}")

                    options = Options()
                    options.add_argument("--headless")
                    options.add_argument("--no-sandbox")
                    options.add_argument("--disable-dev-shm-usage")

                    driver = webdriver.Chrome(options=options)

                    try:
                        driver.get(article_url)
                        time.sleep(3)

                        try:
                            title = WebDriverWait(driver, 20).until(
                                EC.presence_of_element_located((By.XPATH, "//*[@id='title_area']/span"))
                            ).text
                            print(f"타이틀: {title}")
                        except Exception as e:
                            print(f"타이틀을 찾을 수 없습니다: {article_url}")
                            continue

                        try:
                            page_source = driver.page_source
                            soup = BeautifulSoup(page_source, 'html.parser')
                            dic_area = soup.find(id="dic_area")
                            full_text = dic_area.get_text(" ", strip=True)
                            print("기사 본문 (네이버 뉴스 경로):")
                            print(full_text.strip())
                        except Exception as e:
                            print(f"기사 본문을 찾을 수 없습니다: {article_url}")
                            continue

                        naver_news.append({
                            "title": title,
                            "link": article_url,
                            "body": full_text.strip()
                        })

                        articles_fetched += 1

                        if articles_fetched >= max_articles:
                            print(f"원하는 기사 개수 {max_articles}개를 모두 가져왔습니다.")
                            break

                    except Exception as e:
                        print(f"기사 {i+1}에서 오류 발생: {e}")
                    finally:
                        driver.quit()

                params["start"] += 10

            except json.JSONDecodeError:
                print("응답 본문이 JSON 형식이 아닙니다.")
                print("응답 내용:", response.text)

        else:
            print(f"Error Code: {response.status_code}")
            print("응답 내용:", response.text)

    # 기사 데이터를 담은 naver_news를 반환
    return naver_news

In [ ]:
# 원하는 기사의 개수를 5개로 설정하여 호출하고 결과를 저장
naver_news = fetch_naver_news(max_articles=300)

API 호출 횟수: 1
네이버 뉴스 링크 발견: https://n.news.naver.com/mnews/article/662/0000060331?sid=105
타이틀: 외로움·불안함, AI가 해결한다?
기사 본문 (네이버 뉴스 경로):
고려대 ·UNIST , 소셜 챗봇 이용후 영향 분석 4주 3회…본인 이야기 많이 할수록 외로움 감소 고립감·사회적 불안 등 완화…정신건강 관리도 “장기적, 다양한 연령대에서 효과 검증 필요” 사진은 기사의 특정 내용과 관련 없음. 게티이미지뱅크 인공지능( AI )을 활용해 인간의 외로움과 사회불안을 감소시킬 수 있다는 연구 결과가 나왔다. 사회적 고립감을 완화하는 차원을 넘어 정신건강을 증진하는 데도 도움이 될 수 있다는 점에서 정신건강 보조도구로 활용 가능성이 입증됐다. 고려대학교 안암병원 정신건강의학과 조철현 교수 연구팀과 울산과학기술원( UNIST ) 바이오메디컬공학과 정두영 교수팀은 20대 대학생 176명을 대상으로 AI 소셜 챗봇 이용 후의 영향을 분석했다. 소셜 챗봇은 기존 업무 중심 챗봇과 달리 감정적이고 자연스러운 상호작용과 소통을 통해 관계 형성이 가능한 도구다. 이번 연구에서는 인공지능 스타트업 스캐터랩의 ‘이루다 2.0’이 활용됐다. 연구팀은 참가자들의 고립감, 사회적 불안 및 정서 상태를 측정하며 4주 동안 주 3회 이상 챗봇과 상호작용을 하도록 했다. 연구 결과 참가자들의 외로움은 2주 만에 줄기 시작했고 사회불안은 4주 후 유의미한 감소를 보였다. 챗봇에 자신의 이야기를 더 많이 털어놓은 참가자일수록 외로움이 더 크게 감소한 것으로 나타났다. AI 소셜챗봇 사용 전, 평균 27.97로 나타난 고립감 점수는 4주 후 26.39로, 사회적 불안 점수는 초기 평균 25.3에서 4주 후 23.2로 유의미한 감소를 보였다. 사용자 경험 분석에서는 챗봇의 공감 능력과 사용 편의성이 긍정적으로 평가됐으나, 기억력 부족 및 과도한 반응성과 같은 몰입 저해 요인을 발견하며 개선 방향성이 도출됐다. 연구팀은 이번 연구 결

In [ ]:
# 결과를 naver_article 리스트에 저장 (각 기사를 하나의 텍스트로 합침)
naver_article = []
for idx, news in enumerate(naver_news):
    # 제목, 링크, 본문을 하나의 텍스트로 합친 후 리스트에 추가
    article_text = f"{news['title']}\n{news['link']}\n{news['body']}\n"
    naver_article.append(article_text)

In [ ]:
naver_article

['외로움·불안함, AI가 해결한다?\nhttps://n.news.naver.com/mnews/article/662/0000060331?sid=105\n고려대 ·UNIST , 소셜 챗봇 이용후 영향 분석 4주 3회…본인 이야기 많이 할수록 외로움 감소 고립감·사회적 불안 등 완화…정신건강 관리도 “장기적, 다양한 연령대에서 효과 검증 필요” 사진은 기사의 특정 내용과 관련 없음. 게티이미지뱅크 인공지능( AI )을 활용해 인간의 외로움과 사회불안을 감소시킬 수 있다는 연구 결과가 나왔다. 사회적 고립감을 완화하는 차원을 넘어 정신건강을 증진하는 데도 도움이 될 수 있다는 점에서 정신건강 보조도구로 활용 가능성이 입증됐다. 고려대학교 안암병원 정신건강의학과 조철현 교수 연구팀과 울산과학기술원( UNIST ) 바이오메디컬공학과 정두영 교수팀은 20대 대학생 176명을 대상으로 AI 소셜 챗봇 이용 후의 영향을 분석했다. 소셜 챗봇은 기존 업무 중심 챗봇과 달리 감정적이고 자연스러운 상호작용과 소통을 통해 관계 형성이 가능한 도구다. 이번 연구에서는 인공지능 스타트업 스캐터랩의 ‘이루다 2.0’이 활용됐다. 연구팀은 참가자들의 고립감, 사회적 불안 및 정서 상태를 측정하며 4주 동안 주 3회 이상 챗봇과 상호작용을 하도록 했다. 연구 결과 참가자들의 외로움은 2주 만에 줄기 시작했고 사회불안은 4주 후 유의미한 감소를 보였다. 챗봇에 자신의 이야기를 더 많이 털어놓은 참가자일수록 외로움이 더 크게 감소한 것으로 나타났다. AI 소셜챗봇 사용 전, 평균 27.97로 나타난 고립감 점수는 4주 후 26.39로, 사회적 불안 점수는 초기 평균 25.3에서 4주 후 23.2로 유의미한 감소를 보였다. 사용자 경험 분석에서는 챗봇의 공감 능력과 사용 편의성이 긍정적으로 평가됐으나, 기억력 부족 및 과도한 반응성과 같은 몰입 저해 요인을 발견하며 개선 방향성이 도출됐다. 연구팀은 이번 연구 결과를 통해 AI 소셜 챗봇의 이용이 고립감과 사회적 불안을 완화하는 데 효과적일 수 

In [ ]:
# 파일 저장 경로 설정
file_path = "/content/drive/MyDrive/MINI AIFFELTHON/data/AI의 사회적 영향.txt"

# 파일을 쓰기 모드로 열고 naver_article에 있는 내용들을 저장
with open(file_path, 'w', encoding='utf-8') as file:
    for article in naver_article:
        file.write(article + "\n")  # 각 기사를 개별 줄로 저장

print(f"파일이 저장되었습니다: {file_path}")

파일이 저장되었습니다: /content/drive/MyDrive/MINI AIFFELTHON/data/AI의 사회적 영향.txt


In [ ]:
# Define the file path for saving the text file
file_path = '/content/drive/MyDrive/MINI AIFFELTHON/data/naver_article.txt'

# Save the articles as a text file
with open(file_path, 'w', encoding='utf-8') as file:
    for article in naver_article:
        file.write(article + "\n")  # Writing each article in a new line

file_path

'/content/drive/MyDrive/MINI AIFFELTHON/data/naver_article.txt'

In [ ]:
# !pip install sentence-transformers

In [ ]:
from sentence_transformers import SentenceTransformer
import numpy as np

# SentenceTransformer 모델 로드 (미리 학습된 모델을 사용)
model = SentenceTransformer('paraphrase-MiniLM-L6-v2')

# naver_article에서 각 기사를 벡터화
article_vectors = model.encode(naver_article)

# 유저 쿼리 벡터화 예시
query = "최근 AI 업계에서 비디오 생성 모델이 뭐가 있을까? 그리고 그 모델들의 성능 비교는 어떻게 되고, 앞으로의 전망은 어때?"
query_vector = model.encode([query])

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity

# 쿼리 벡터와 기사 벡터 간 유사도 계산
similarities = cosine_similarity(query_vector, article_vectors)

# 가장 유사한 기사 인덱스 찾기
best_match_idx = np.argmax(similarities)
print(f"가장 유사한 기사는 {best_match_idx + 1}번 기사입니다.")

가장 유사한 기사는 18번 기사입니다.


In [ ]:
!pip install langchain
!pip install langchain_community
!pip install --upgrade langchain
!pip install --upgrade langchain_community
!pip install tiktoken
!pip install -U langchain-openai

  Using cached openai-1.59.9-py3-none-any.whl.metadata (27 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.3/54.3 kB 2.3 MB/s eta 0:00:00
Using cached openai-1.59.9-py3-none-any.whl (455 kB)
  Attempting uninstall: openai
    Found existing installation: openai 0.28.0
    Uninstalling openai-0.28.0:
      Successfully uninstalled openai-0.28.0


In [ ]:
# !pip install openai==0.28

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 2.3 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.59.9
    Uninstalling openai-1.59.9:
      Successfully uninstalled openai-1.59.9


In [ ]:
# 파일 경로 설정
file_path = '/content/drive/MyDrive/MINI AIFFELTHON/data/naver_article.txt'

# 텍스트 파일 읽기
with open(file_path, 'r', encoding='utf-8') as file:
    # 파일 내용을 읽어서 줄바꿈 두 번을 기준으로 데이터를 분리
    text = file.read()
    naver_article = text.split('\n\n')  # 줄바꿈 두 번으로 데이터 구분

# 결과 확인
print(naver_article[:5])  # 첫 5개의 기사를 출력 (길이가 길면 일부만 출력)

['한발 늦게 \'AI 원주민\' 되겠다는 카카오...성능 발표는 \'소심하게\'\nhttps://n.news.naver.com/mnews/article/138/0002184952?sid=105\n[디지털데일리 이건한 기자] 지난 22일 자체 개발한 통합 인공지능( AI ) 플랫폼 \'카나나( KANANA )\'를 공개한 카카오가 조직문화도 \'AI 네이티브( Native , 본질적인·원주민)\'로 전환 중인 점을 강조하고 나섰다. 카카오가 최근 주요 경쟁사들 대비 AI 혁신 및 사업 전환에 뒤졌다는 평가를 받는 가운데, 우선 내부에서부터 \'AI DNA\' 를 심고 추격하겠단 의지로 풀이된다. 다만 구체적인 경쟁력을 강조해야 할 대목에선 소극적 태도를 보여 일부 아쉬움을 남겼다. 정규된 카카오 CTO 가 이프카카오 2일차 키노트에서 \'AI 네이티브\' 전략을 발표하고 있다. [ⓒ 이프카카오 라이브 영상 갈무리] AI 네이티브 대전환, 탐색 마치고 혁신으로 카카오의 네이티브 AI 전략은 \'이프카카오( if kakao ) AI 2024\' 행사 2일차인 23일 키노트에서 정규돈 카카오 최고기술책임자( CTO )가 직접 발표했다. 정 CTO 는 "현재 엄청난 자본력을 바탕으로 급진적 AI 기술 발전이 이뤄지는 (세계 AI 산업) 모습을 보며 어떤 대응을 할지 기대와 두려움도 느껴진다"며 "이를 위해 카카오는 AI 네이티브 전략을 택한 것"이라고 말했다. 이어 "그 전환 과정의 측정 및 관리를 위해 카카오 자체적으로 AI 네이티브 성숙 레벨을 정한 것"이라고 설명했다. 카카오 네이티브 AI 성숙도 레벨은 ▲탐색 ▲적용 ▲혁신 ▲일상으로 구분된다. 발표 내용에 따르면 카카오는 현재 지난 2년여의 탐색 단계를 거쳐 적용 및 혁신으로 나아가는 단계다. 탐색은 우선 사내에 AI 를 전파하고 임직원들이 관련 경험을 직접 축적하는 시기다. 정 CTO 는 "좋은 서비스를 만들려면 먼저 직접 경험해야 한다는 사내 철학에 근거한 것"이라며 "사내 교육 및 세미나, 테크톡, AI

In [ ]:
naver_article

['한발 늦게 \'AI 원주민\' 되겠다는 카카오...성능 발표는 \'소심하게\'\nhttps://n.news.naver.com/mnews/article/138/0002184952?sid=105\n[디지털데일리 이건한 기자] 지난 22일 자체 개발한 통합 인공지능( AI ) 플랫폼 \'카나나( KANANA )\'를 공개한 카카오가 조직문화도 \'AI 네이티브( Native , 본질적인·원주민)\'로 전환 중인 점을 강조하고 나섰다. 카카오가 최근 주요 경쟁사들 대비 AI 혁신 및 사업 전환에 뒤졌다는 평가를 받는 가운데, 우선 내부에서부터 \'AI DNA\' 를 심고 추격하겠단 의지로 풀이된다. 다만 구체적인 경쟁력을 강조해야 할 대목에선 소극적 태도를 보여 일부 아쉬움을 남겼다. 정규된 카카오 CTO 가 이프카카오 2일차 키노트에서 \'AI 네이티브\' 전략을 발표하고 있다. [ⓒ 이프카카오 라이브 영상 갈무리] AI 네이티브 대전환, 탐색 마치고 혁신으로 카카오의 네이티브 AI 전략은 \'이프카카오( if kakao ) AI 2024\' 행사 2일차인 23일 키노트에서 정규돈 카카오 최고기술책임자( CTO )가 직접 발표했다. 정 CTO 는 "현재 엄청난 자본력을 바탕으로 급진적 AI 기술 발전이 이뤄지는 (세계 AI 산업) 모습을 보며 어떤 대응을 할지 기대와 두려움도 느껴진다"며 "이를 위해 카카오는 AI 네이티브 전략을 택한 것"이라고 말했다. 이어 "그 전환 과정의 측정 및 관리를 위해 카카오 자체적으로 AI 네이티브 성숙 레벨을 정한 것"이라고 설명했다. 카카오 네이티브 AI 성숙도 레벨은 ▲탐색 ▲적용 ▲혁신 ▲일상으로 구분된다. 발표 내용에 따르면 카카오는 현재 지난 2년여의 탐색 단계를 거쳐 적용 및 혁신으로 나아가는 단계다. 탐색은 우선 사내에 AI 를 전파하고 임직원들이 관련 경험을 직접 축적하는 시기다. 정 CTO 는 "좋은 서비스를 만들려면 먼저 직접 경험해야 한다는 사내 철학에 근거한 것"이라며 "사내 교육 및 세미나, 테크톡, AI

In [ ]:
!pip install langchain-openai

In [ ]:
import openai
import numpy as np
import faiss
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

# OpenAI API Key 설정
openai.api_key = ""

# 여러 임베딩 모델 로드 (교체할 수 있도록 설정)
models = {
    "paraphrase-MiniLM-L6-v2": SentenceTransformer('paraphrase-MiniLM-L6-v2'),
    "all-MiniLM-L6-v2": SentenceTransformer('all-MiniLM-L6-v2')
}

# 벡터 DB 생성 함수
def create_faiss_index(articles, model_name="paraphrase-MiniLM-L6-v2"):
    model = models[model_name]
    article_vectors = model.encode(articles)  # 각 기사 벡터화

    # FAISS 인덱스 생성
    faiss_index = faiss.IndexFlatL2(len(article_vectors[0]))  # L2 거리 기반
    faiss_index.add(np.array(article_vectors))

    return faiss_index

# 유저 쿼리 벡터화 및 유사도 계산
def retrieve_similar_articles(query, faiss_index, model_name="paraphrase-MiniLM-L6-v2", top_k=3):
    model = models[model_name]
    query_vector = model.encode([query])  # 유저 쿼리 벡터화

    # 쿼리 벡터와 기사 벡터 간 유사도 계산
    distances, indices = faiss_index.search(np.array(query_vector), top_k)
    return indices[0], distances[0]

# OpenAI로 답변 생성
def generate_answer_with_openai(context, query):
    messages = [
        {"role": "system", "content": "You are a helpful assistant."},
        {"role": "user", "content": f"질문: {query}"},
        {"role": "assistant", "content": f"가장 관련 있는 기사 내용:\n{context}\n답변:"}
    ]

    response = openai.ChatCompletion.create(
        model="gpt-3.5-turbo",  # OpenAI의 최신 모델로 변경
        messages=messages,
        max_tokens=200,  # 필요한 길이만큼 생성
        temperature=0.7  # 창의적인 응답을 위한 설정
    )

    return response.choices[0].message['content'].strip()

In [ ]:
# 벡터 DB 생성
faiss_index = create_faiss_index(naver_article, model_name="paraphrase-MiniLM-L6-v2")

# 쿼리 예시
query = "최근 AI 업계에서 비디오 생성 모델이 뭐가 있을까? 그리고 그 모델들의 성능 비교는 어떻게 되고, 앞으로의 전망은 어때?"

# 유사한 기사 검색
top_k = 3
indices, distances = retrieve_similar_articles(query, faiss_index, model_name="paraphrase-MiniLM-L6-v2", top_k=top_k)

# 가장 유사한 기사 내용 추출
best_articles = [naver_article[i] for i in indices]
# best_article = naver_article[best_match_idx]  # 유사도 가장 높은 기사

# 제목, 링크, 본문을 추출
best_article_title = best_article.split('\n')[0]  # 첫 번째 줄은 기사 제목
best_article_link = best_article.split('\n')[1]   # 두 번째 줄은 기사 링크
best_article_content = "\n".join(best_article.split('\n')[2:])  # 세 번째 줄부터는 기사 본문

# OpenAI로 생성된 답변 받기 (가장 유사한 기사 기반)
def generate_answer_with_openai(context, query):
    messages = [
        {"role": "system", "content": "You are a helpful assistant."},
        {"role": "user", "content": f"질문: {query}"},
        {"role": "assistant", "content": f"가장 관련 있는 기사 내용:\n{context}\n답변:"}
    ]

    response = openai.ChatCompletion.create(
        model="gpt-3.5-turbo",  # OpenAI의 최신 모델로 변경
        messages=messages,
        max_tokens=200,  # 필요한 길이만큼 생성
        temperature=0.7  # 창의적인 응답을 위한 설정
    )

    return response.choices[0].message['content'].strip()

# 가장 유사한 기사 내용 기반으로 답변 생성
answer = generate_answer_with_openai(best_article_content, query)

print(f"기사 링크: {best_article_link}")
print(f"{answer}")

기사 링크: https://n.news.naver.com/mnews/article/277/0005311360?sid=101
최근 AI 업계에서 비디오 생성 모델 중 하나로 중국의 텐센트가 개발한 거대언어모델 '훈위안'이 소개되었습니다. '훈위안'은 매개변수 수가 1000억개 이상으로, GPT3와 라마2보다 높은 성능을 자랑하며 중국어와 영어를 지원하는 장점을 가지고 있습니다. 또한 '환각( AI의 거짓말)' 문제를 개선하여 신뢰성을 높였다고 합니다. 텐센트는 웨이보와 위챗과 같은 대


#### 본문이 포함된 Web PATH 경로 에러
* 특정 언론사(네이버 뉴스 등)에서만(동일 형식을 가지는) 추출
* 웹 페이지 (URL 패턴 - EX) page==1 ) 추출 - 위와 동일

### 구글

In [ ]:
from google.oauth2 import service_account
from googleapiclient.discovery import build

# JSON 키 - GCP
SERVICE_ACCOUNT_FILE = '/content/drive/MyDrive/MINI AIFFELTHON/data/google-search-api.json'

# 스코프
SCOPES = ['https://www.googleapis.com/auth/cse']

# JSON Credentials
credentials = service_account.Credentials.from_service_account_file(
    SERVICE_ACCOUNT_FILE, scopes=SCOPES
)

# Custom Search Engine API 설정
service = build('customsearch', 'v1', credentials=credentials)

# Custom Search Engine ID (CSE ID)
CSE_ID = '43d5ba13375cf4a95'

# 검색 함수
def google_custom_search(query, num_results=3):
    try:
        response = service.cse().list(
            q=query,
            cx=CSE_ID,
            num=num_results
        ).execute()
        return response.get('items', [])
    except Exception as e:
        print(f"Error: {e}")
        return []

# # 검색 실행
# query = "Python tutorial"
# results = google_custom_search(query)
# for i, item in enumerate(results, start=1):
#     print(f"[{i}] {item['title']}\nURL: {item['link']}\n")

[1] The Python Tutorial — Python 3.13.1 documentation
URL: https://docs.python.org/3/tutorial/index.html

[2] Python Tutorial
URL: https://www.w3schools.com/python/

[3] Python Tutorial: Learn Python Programming for Free
URL: https://www.tutorialspoint.com/python/index.htm



In [ ]:
from google.oauth2 import service_account
from googleapiclient.discovery import build
from transformers import BartForConditionalGeneration, PreTrainedTokenizerFast
import requests
from bs4 import BeautifulSoup
import time

# JSON 키 PATH
SERVICE_ACCOUNT_FILE = '/content/drive/MyDrive/MINI AIFFELTHON/data/google-search-api.json'
SCOPES = ['https://www.googleapis.com/auth/cse']

# 크리덴셜 초기화
credentials = service_account.Credentials.from_service_account_file(
    SERVICE_ACCOUNT_FILE, scopes=SCOPES
)

service = build('customsearch', 'v1', credentials=credentials)

CSE_ID = '43d5ba13375cf4a95'

# KoBART 모델 & 토크나이저
model = BartForConditionalGeneration.from_pretrained("hyunwoongko/kobart")
tokenizer = PreTrainedTokenizerFast.from_pretrained("hyunwoongko/kobart")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

You passed along `num_labels=3` with an incompatible id to label map: {'0': 'NEGATIVE', '1': 'POSITIVE'}. The number of labels wil be overwritten to 2.


pytorch_model.bin:   0%|          | 0.00/496M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/337 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.05M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/109 [00:00<?, ?B/s]

In [ ]:
# Google Custom Search API
def google_custom_search(query, num_results=2): # 2개만. 일일 100회 제한
    try:
        response = service.cse().list(
            q=query,
            cx=CSE_ID,
            num=num_results
        ).execute()
        return response.get('items', [])
    except Exception as e:
        print(f"Error: {e}")
        return []

# 본문 크롤링 - BeautifulSoup
def extract_article_content(url):
    try:
        headers = {"User-Agent": "Mozilla/5.0"}
        response = requests.get(url, headers=headers)
        if response.status_code == 200:
            soup = BeautifulSoup(response.content, "html.parser")
            # HTML에서 본문 추출 (네이버 XPath 대체)
            paragraphs = soup.find_all("p")
            content = " ".join(p.get_text(strip=True) for p in paragraphs)
            return content
        else:
            print(f"Failed to fetch URL: {url} with status code {response.status_code}")
            return ""
    except Exception as e:
        print(f"Error while fetching article content: {e}")
        return ""

# 텍스트 요약 함수
def summarize_text(text):
    try:
        inputs = tokenizer.encode("summarize: " + text, return_tensors="pt", max_length=1024, truncation=True)
        summary_ids = model.generate(inputs, max_length=150, min_length=40, length_penalty=2.0, num_beams=4, early_stopping=True)
        return tokenizer.decode(summary_ids[0], skip_special_tokens=True)
    except Exception as e:
        print(f"요약 중 에러: {e}")
        return "요약 실패"

# 4. RAG 검색 함수 - 쿼리 벡터 유사도 계산 X
def rag_pipeline(query):
    search_results = google_custom_search(query, num_results=3)
    results = []

    for item in search_results:
        link = item['link']
        title = item['title']
        print(f"Processing: {title} - {link}")

        # 본문 크롤링
        content = extract_article_content(link)
        if content:
            # 본문 요약
            summary = summarize_text(content)
            results.append({"title": title, "link": link, "summary": summary})
        else:
            results.append({"title": title, "link": link, "summary": "본문 크롤링 실패"})

    return results

In [ ]:
# Google Custom Search API(검색 사이트)가 자체적으로 query 유사도를 계산
query = "AI 최신 기술"
results = rag_pipeline(query)

for idx, result in enumerate(results, start=1):
    print(f"\n[{idx}] 제목: {result['title']}\n요약: {result['summary']}\n링크: {result['link']}\n")

Processing: 제미나이의 새로운 AI 리서치 어시스턴트, '딥 리서치(Deep Research) - https://blog.google/intl/ko-kr/company-news/technology/ai-deep-research-kr/
Processing: 챗GPT AI검색 출시, 네이버 구글 천하 뒤흔들까 - https://www.mediatoday.co.kr/news/articleView.html?idxno=322067
Processing: 제미나이 2.0 출시: 에이전트 시대를 위한 구글의 새로운 AI 모델 - https://blog.google/intl/ko-kr/company-news/technology/gemini-2-0-kr/

[1] 제목: 제미나이의 새로운 AI 리서치 어시스턴트, '딥 리서치(Deep Research)
요약: 합니다. 에서 제미미 순 순 순 순 순 순 순 순 순 순 순 것 것 오늘부터 전세계 제미나이 어드밴스드 이용자는 시간은 절약하고 더 심층적인 연구를 돕는  ‘딥 리서치’를 영어로 이용할 수 있습니다. 또한, 이제 웹에서 제미나이 2.0 실험 모델에 액세스할 수 있습니다. 오늘 구글은 제미나이 어드밴스드(Gemini Advanced)의 새로운 기능인 ‘딥 리서치(Deep Research)’와 제미나이 2.0 실험 모델을 발표합니다. 전세계 제미나이 어드밴스드 이용자는 오늘부터 영어로 딥 리서치를 사용할 수 있습니다. 딥 리서치는 AI를
링크: https://blog.google/intl/ko-kr/company-news/technology/ai-deep-research-kr/


[2] 제목: 챗GPT AI검색 출시, 네이버 구글 천하 뒤흔들까
요약: 이다. 위험이 위험이 않고ummarize: AI 미디어 파도 챗GPT 개발사인 오픈AI가 네이버, 구글에 이어 AI검색 서비스를 선보였다. 생성형AI의 검색 서비스 접목이 이어지면서 장기적으로 포털·검색엔진 서비스의 지각변동이 예상된다. 오픈AI는 지난달 31일 AI검

In [ ]:
# JSON 키 - GCP
SERVICE_ACCOUNT_FILE = '/content/drive/MyDrive/MINI AIFFELTHON/data/google-search-api.json'

# 스코프
SCOPES = ['https://www.googleapis.com/auth/cse']

# JSON Credentials
credentials = service_account.Credentials.from_service_account_file(
    SERVICE_ACCOUNT_FILE, scopes=SCOPES
)

# Custom Search Engine API 설정
service = build('customsearch', 'v1', credentials=credentials)

# Custom Search Engine ID (CSE ID)
CSE_ID = '43d5ba13375cf4a95'

In [ ]:
# Google Custom Search API
def google_custom_search(query, num_results=1):  # 2개만. 일일 100회 제한
    try:
        response = service.cse().list(
            q=query,
            cx=CSE_ID,
            num=num_results
        ).execute()
        return response.get('items', [])
    except Exception as e:
        print(f"Error: {e}")
        return []


# 본문 크롤링 - BeautifulSoup
def extract_article_content(url):
    try:
        headers = {"User-Agent": "Mozilla/5.0"}
        response = requests.get(url, headers=headers)
        if response.status_code == 200:
            soup = BeautifulSoup(response.content, "html.parser")
            # HTML에서 본문 추출 (네이버 XPath 대체)
            paragraphs = soup.find_all("p")
            content = " ".join(p.get_text(strip=True) for p in paragraphs)
            return content
        else:
            print(f"Failed to fetch URL: {url} with status code {response.status_code}")
            return ""
    except Exception as e:
        print(f"Error while fetching article content: {e}")
        return ""


# 긴 텍스트를 파일에 저장하는 함수
def save_long_text_to_file(results, file_path):
    with open(file_path, 'w', encoding='utf-8') as f:
        for result in results:
            title = result['title']
            link = result['link']
            content = result['content']

            # 파일에 제목과 링크 저장
            f.write(f"Title: {title}\n")
            f.write(f"Link: {link}\n")
            f.write("Content:\n")

            # 긴 본문을 적절히 나누어 저장 (일단 1000자씩)
            chunk_size = 1000
            for i in range(0, len(content), chunk_size):
                f.write(content[i:i+chunk_size] + "\n")

            f.write("\n\n")


# 4. RAG 검색 함수 - 쿼리 벡터 유사도 계산 X
def rag_pipeline(query):
    search_results = google_custom_search(query, num_results=1)
    results = []

    for item in search_results:
        link = item['link']
        title = item['title']
        print(f"Processing: {title} - {link}")

        # 본문 크롤링
        content = extract_article_content(link)
        if content:
            results.append({"title": title, "link": link, "content": content})
        else:
            results.append({"title": title, "link": link, "content": "본문 크롤링 실패"})

    # 결과를 JSON 형태로 변환
    data = json.dumps(results, ensure_ascii=False, indent=4)

    # 결과를 텍스트 파일로 저장
    save_long_text_to_file(results, '/content/drive/MyDrive/article_content.txt')

    return data

In [ ]:
# Google Custom Search API(검색 사이트)가 자체적으로 query 유사도를 계산
query = "AI 최신 기술"
results_json = rag_pipeline(query)

# 출력 확인
print(results_json)

Processing: 2024년 AI/ML 20대 최신 기술 연구 동향 (April 1) | by Jonghong Jeon ... - https://medium.com/@favorable_eminence_oyster_546/2024%EB%85%84-ai-ml-17%EB%8C%80-%EC%B5%9C%EC%8B%A0-%EA%B8%B0%EC%88%A0-%EC%97%B0%EA%B5%AC-%EB%8F%99%ED%96%A5-april-1-788f3cc4f6b2
[
    {
        "title": "2024년 AI/ML 20대 최신 기술 연구 동향 (April 1) | by Jonghong Jeon ...",
        "link": "https://medium.com/@favorable_eminence_oyster_546/2024%EB%85%84-ai-ml-17%EB%8C%80-%EC%B5%9C%EC%8B%A0-%EA%B8%B0%EC%88%A0-%EC%97%B0%EA%B5%AC-%EB%8F%99%ED%96%A5-april-1-788f3cc4f6b2",
        "content": "Sign up Sign in Sign up Sign in Jonghong Jeon Follow -- 1 Share 이런 기술이 등장했다는게 놀랍네요. 올해는 Claude 3의 도움을 받아 최근 개발된 신기술들을 구체적으로 정리해봤습니다. -- -- 1 International standardization expert on AI/ML Help Status About Careers Press Blog Privacy Terms Text to speech Teams"
    }
]


In [ ]:
import time
import os
import json
from google.oauth2 import service_account
from googleapiclient.discovery import build
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup

In [ ]:
# JSON 키 - GCP
SERVICE_ACCOUNT_FILE = '/content/drive/MyDrive/MINI AIFFELTHON/data/google-search-api.json'

# 스코프
SCOPES = ['https://www.googleapis.com/auth/cse']

# JSON Credentials
credentials = service_account.Credentials.from_service_account_file(
    SERVICE_ACCOUNT_FILE, scopes=SCOPES
)

# Custom Search Engine API 설정
service = build('customsearch', 'v1', credentials=credentials)

# Custom Search Engine ID (CSE ID)
CSE_ID = '43d5ba13375cf4a95'

In [ ]:
# 검색 쿼리 & API 호출
def search_query(query, start=1, num_results=1):
    res = service.cse().list(
        q=query,
        cx=CSE_ID,
        start=start,
        num=num_results  # 검색 결과 수
    ).execute()
    return res

# Selenium을 설정하기 위한 Chrome 옵션
def create_driver():
    chrome_options = Options()
    chrome_options.add_argument('--headless')  # 백그라운드 실행
    chrome_options.add_argument('--no-sandbox')
    chrome_options.add_argument('--disable-dev-shm-usage')
    driver = webdriver.Chrome(options=chrome_options)
    return driver

# 결과 추출
def get_search_results(query, num_results=1):
    results = []

    # 검색 쿼리 이용
    search_results = search_query(query, num_results=num_results)

    # 타이틀과 링크 추출
    for item in search_results['items']:
        title = item['title']
        link = item['link']

        # Selenium을 사용해 웹 페이지 내부에서 본문 추출
        driver = create_driver()
        driver.get(link)

        try:
            # 10초 대기
            WebDriverWait(driver, 10).until(
                EC.presence_of_element_located((By.TAG_NAME, "body"))
            )

            # 본문 데이터를 추출 - 전부
            body = driver.find_element(By.TAG_NAME, "body").text

            # 결과 json
            results.append({
                'title': title,
                'link': link,
                'body': body
            })
        except Exception as e:
            print(f"Error while scraping {link}: {e}")
        finally:
            driver.quit()

    return results

In [ ]:
query = "AI 최신 발전 근황"
num_results = 5  # 결과 수 초기화
search_results = get_search_results(query, num_results)

# 결과 출력
for result in search_results:
    print(f"Title: {result['title']}")
    print(f"Link: {result['link']}")
    print(f"Body: {result['body']}")

Title: 298. 한국 AI 발전 근황: AI 기본법부터 최신 기술 도입 사례까지
Link: https://guguuu.com/entry/298-korea-ai-development-trends
Body: 본문 바로가기
구구 구구
검색
홈
AI
298. 한국 AI 발전 근황: AI 기본법부터 최신 기술 도입 사례까지
by 구구 구구 2024. 12. 1.
꼭 키워드에 한국 넣으면 국기 넣는게 끝인가, dall-e
  한국 AI 발전 근황: AI 기본법부터 최신 기술 도입 사례까지
  01. 서론
1) 한국의 글로벌 AI 강국 도전 현황
한국은 최근 AI 기술과 규제 정비를 통해 글로벌 AI 강국으로 도약하려는 노력을 이어가고 있습니다. AI 기본법 제정, AI안전연구소 설립, 대기업들의 AI 도입 등 다양한 활동이 주목받고 있습니다. 이러한 움직임은 단순히 기술 개발에 그치지 않고, 신뢰성과 안전성을 보장하면서 산업 전반의 혁신을 주도하려는 의지를 보여줍니다.
  특히, AI 기본법은 AI 기술의 윤리적 사용과 국민의 기본권 보장을 위한 법적 기반을 마련함으로써 한국이 국제 사회에서 AI 선진국으로 자리 잡는 데 기여할 것으로 기대됩니다.
  2) 한국의 AI 주요 이슈 요약 소개
한국의 AI 발전은 기술 혁신과 정책 정비가 조화를 이루며 빠르게 진행되고 있습니다. AI 기술 도입 사례로는 현대오토에버와 KT, SK브로드밴드 등 대기업이 AI 기술을 활용해 업무 효율성을 극대화하고, 맞춤형 서비스를 제공하고 있습니다.
  또한, AI안전연구소 설립은 신뢰할 수 있는 AI 기술을 개발하고, 국제 규제 체계를 학습하며 글로벌 시장에서 경쟁력을 높이는 데 중점을 두고 있습니다. 이러한 다양한 이슈들은 한국이 AI 기술과 정책 모두에서 선도적인 위치를 차지하려는 움직임을 보여줍니다.
  02. 한국 AI 기술 발전의 주요 이슈
1) AI 기본법 제정과 의미
AI 기술과 산업 발전을 위한 법적 기반
AI 기본법은 국회를 통과하며 AI 기술 발전을 촉진하고, 신뢰할 